In [40]:
import numpy as np
from operator import add
import pandas as pd
import pickle
from random import randint, random
import warnings
warnings.filterwarnings('ignore')

In [41]:
n_features = 25
with open('./trained_networks/rr_%d_data.pkl' % n_features, 'rb') as result:
    CLF = pickle.load(result)

def main():
    target = 100
    p_count = 100
    i_length = n_features
    i_min = -10
    i_max = 10
    p = population(p_count, i_length, i_min, i_max)
    fitness_history = [grade(p, target),]
    for i in xrange(100):
        p = evolve(p, target)
        fitness_history.append(grade(p, target))
        solution = p
    solution = pd.DataFrame(solution)
    solution.to_csv('./data/genalgo_results.csv')
    for datum in fitness_history:
        print(datum)


def individual(length, minimum, maximum):
    """
    Create a member of the population.
    :param length:
    :param minimum:
    :param maximum:
    :return:
    """
    return [np.random.uniform(minimum, maximum) for x in xrange(length)]


def population(count, length, minimum, maximum):
    """
    Create a number of individuals (i.e. a population).

    :param count: the number of individuals in the population
    :param length: the number of values per individual
    :param minimum: the minimum possible value in an individual's list of values
    :param maximum: the maximum possible value in an individual's list of values

    """
    return [individual(length, minimum, maximum) for x in xrange(count)]


def fitness(individuals, target):
    """
    Determine the fitness of an individual. Higher is better.

    :param individuals: the individual to evaluate
    :param target: the target number individuals are aiming for
    """
    print np.array(individuals)
    #individuals = individuals.reshape((1, -1))
    activity = CLF.predict(np.array(individuals))

    return abs(target - activity)


def grade(pop, target):
    """
    Find average fitness for a population.
    :param pop:
    :param target:
    :return:
    """
    summed = reduce(add, (fitness(x, target) for x in pop))
    return summed / (len(pop) * 1.0)


def evolve(pop, target, retain=0.2, random_select=0.05, mutate=0.01):
    """
    :param pop:
    :param target:
    :param retain:
    :param random_select:
    :param mutate:
    :return: parents
    """
    graded = pd.DataFrame([(fitness(x, target), x) for x in pop],
                          columns=['fitness', 'descriptors']).sort_values(by='fitness', ascending=0)
    # Shape -> (100, 2)
    graded.reset_index(drop=True, inplace=True)
    graded = np.array(graded['descriptors'])
    retain_length = int(len(graded)*retain)
    parents = graded[:retain_length].tolist()
    # randomly add other individuals to promote genetic diversity
    for individuals in graded[retain_length:]:
        if random_select > random():
            parents.append(individuals)
    # mutate some individuals
    for individuals in parents:
        if mutate > random():
            pos_to_mutate = randint(0, len(individuals)-1)
            # this mutation is not ideal, because it restricts the range of possible values,
            # but the function is unaware of the min/max values used to create the individuals.
            individuals[pos_to_mutate] = randint(np.floor(min(individuals)),
                                                 np.ceil(max(individuals)))
    # crossover parents to create children
    parents_length = len(parents)
    desired_length = len(pop) - parents_length
    children = []
    while len(children) < desired_length:
        male = randint(0, parents_length-1)
        female = randint(0, parents_length-1)
        if male != female:
            male = parents[male]
            female = parents[female]
            half = len(male) / 2
            child = male[:half] + female[half:]
            children.append(child)
    parents.extend(children)
    return parents

In [42]:
main()

[-2.19943849 -5.72399807 -8.9499643  -1.51314541  7.61991546  1.23512715
 -2.22077917  5.17739269  2.61439549  2.3128735  -4.81437572 -3.79158992
 -1.66567906 -9.72452939 -4.24025189 -9.02427727 -0.03428078  7.93970765
  4.78955963 -9.80745887 -1.31680518  2.67701744 -1.36162291 -4.0270459
  7.45266264]
[ 9.8422944   0.52000198 -8.12291517  2.19782222 -9.37401541  3.41621584
 -4.3536421   5.85202083  5.10474933  6.48413677  1.17535395 -9.85547924
  1.96488285 -3.95865448 -6.41100478  3.92186036 -9.64609433 -5.06915274
  3.61646058  4.92642927 -3.41434806 -8.48884479 -8.95664685 -3.11033665
 -8.11589437]
[-1.21903832  9.24486395  1.9043168   4.4209572   3.02073234  0.45936172
 -3.92388956 -2.21914617  1.92636638  1.57721691 -7.63101361  7.89513405
  3.67355154 -9.79294924  1.99558945 -1.66584421 -0.86937377 -4.06508691
  9.78855972 -2.05896836 -7.94652795 -5.01718997  4.42230965 -5.46838851
 -9.51184276]
[ 0.59528171 -6.39117084 -1.22512476 -6.20958311  5.42006844 -9.75147279
 -8.764748

In [37]:
print solution

NameError: name 'solution' is not defined